In [11]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [12]:
import socket
print(socket.gethostname())

rhea


In [13]:
from pipelines import emission


from pipelines.nets.object_detection.yolo.brambox import boxes as bbb
from pipelines.nets.object_detection.yolo.brambox.boxes.util import visual as vis
from pipelines.nets.object_detection.yolo.brambox.boxes.detections.detection import *


In [14]:
import ast
def format_ultralytics_detections( img_dir, dets_dir = None, weights_cfg_file = '/media/kuser/datastore/nebula/pipelines/best_models/OT_model_nobdd/cfg.json'):    
    with open('/media/kuser/datastore/nebula/pipelines/configs/entanglement_cfg.tml', 'r') as tmlfile:
        cfg = toml.load(tmlfile)
        
    with open(weights_cfg_file, 'r') as f:
        weights_cfg = json.load(f)
        weights_cfg['labels'] = [str(x) for x in ast.literal_eval(weights_cfg['labels'])]

        
    if not dets_dir:
        dets_dir = os.path.join(img_dir, 'annotations')
        os.makedirs(dets_dir, exist_ok = True)
    yolov3_dir = cfg['entanglement']['yolov3_dir']
    src_model_cfg = os.path.join(yolov3_dir, 'cfg', 'yolov3.cfg')
    src_data_cfg = os.path.join(yolov3_dir, 'cfg', 'yolov3.data')

    # Override model config
    dest_cfg_dir = os.path.abspath(os.path.join(dets_dir, os.pardir, 'cfg'))
    os.makedirs(dest_cfg_dir,exist_ok=True)
    yolo_cfg = format_model_config(weights_cfg, src_model_cfg, os.path.join(dest_cfg_dir, os.path.split(src_model_cfg)[-1]))

    current_data_cfg = parse_data_config(src_data_cfg)
    os.makedirs(os.path.join(dets_dir, 'data'), exist_ok = True)
    os.makedirs(os.path.join(dets_dir, 'cfg'), exist_ok = True)
    current_data_cfg = inject_data_config(dets_dir, current_data_cfg, tracking_classes)
    current_data_cfg_path = save_data_config(current_data_cfg, os.path.join(dets_dir, 'cfg', os.path.split(src_data_cfg)[-1]))

    
    # Run yolo to obtain detections
    emitter = emission.UltralyticsDetector(weights_file = weights_cfg['weights_path'],  cfg = yolo_cfg, labels = weights_cfg['labels']  )
    dets = emitter.emit(img_dir, detection_threshold = 0.40)
    
    return dets

import urllib
import ntpath
from pipelineapi import PipelineAPI
import os
import json
import glob


def path_leaf(path):
    if urllib.parse.urlparse(path).scheme != "" or os.path.isabs(path):
        path = os.path.split(path)[-1]
    head, tail = ntpath.split(path)
    return tail or ntpath.basename(head)


def parse_data_config(path):
        """Parses the data configuration file"""
        options = dict()
        with open(path, 'r') as fp:
            lines = fp.readlines()
        for line in lines:
            line = line.strip()
            if line == '' or line.startswith('#'):
                continue
            key, value = line.split('=')
            options[key.strip()] = value.strip()
        return options

    
def inject_data_config(dets_dir, data_config, tracking_classes):
    data_config['classes'] = len(tracking_classes)
    data_config['names'] = generate_names_cfg(dets_dir, tracking_classes)
    return data_config


def generate_names_cfg(dets_dir, tracking_classes):
    names_config = os.path.join(dets_dir, 'labels.names')
    with open(names_config, 'w+') as writer:
        for category in tracking_classes:
            writer.write(category.strip().replace('\'', '').replace('[', '').replace(']', '') +'\n')
    return names_config


def save_data_config(data_config, path, overwrite = False):
    """Saves the yolo-v3 data configuration file"""
    if not os.path.exists(path) or overwrite == True:
        with open(path, 'w') as writer:
            [writer.write(str(k)+'='+str(v)+'\n') for k,v in data_config.items()]
    return path


def format_model_config(weights_cfg, model_config_path, destination_cfg):
    anchors =str(weights_cfg['anchors']).replace('[','').replace(']','')
    dataset_category_names =weights_cfg['labels']


    content = None
    with open(model_config_path, 'r') as f:
        content = f.readlines()
        for idx, line in enumerate(content):
            key_vals = line.split('=')
            if len(key_vals) > 1:
                if 'anchors' in key_vals[0]:
                    key_vals[1] = str(anchors)
                    content[idx] = "=".join(key_vals)
                elif 'anchors' in key_vals[0]:
                    key_vals[1] = str(anchors)
                    content[idx] = "=".join(key_vals)
                elif 'classes' in key_vals[0]:
                    key_vals[1] = str(len(dataset_category_names))
                    content[idx] = "=".join(key_vals)
                elif 'filters' in key_vals[0] and ('yolo' in content[idx+2] or 'yolo' in content[idx+3] or 'yolo' in content[idx+4]):
                    key_vals[1] = str((len(dataset_category_names)+5)*3)
                    content[idx] = "=".join(key_vals)

                else:
                    for key, val in weights_cfg.items():
                        if len(key_vals) > 1 and str(key) in key_vals[0]:
                            key_vals[1] = str(val)
                            content[idx] = "=".join(key_vals)
                            break

    # Save model cfg #
    os.makedirs(os.path.dirname(destination_cfg), exist_ok = True)
    with open(destination_cfg, 'w') as f:        
        f.write("\n".join([c.strip("\n") for c in content]))
    return destination_cfg

In [17]:
import os
from moviepy.editor import VideoFileClip
from moviepy.editor import ImageSequenceClip
from moviepy.editor import CompositeVideoClip

from IPython.display import HTML
from PIL import Image
import shutil
import glob
import json
import toml
import cv2


yolo_python = '/opt/anaconda3/envs/py36/bin/python'
atm_dir = '~/atm/tools/'
cam_num = 7
extraction_dir = '/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam{}/'.format(cam_num)
save_dir = '/home/kuser/Desktop/demo_files/mp4cam{}/'.format(cam_num)

if not os.path.exists(extraction_dir):
    os.makedirs(extraction_dir)
if not os.path.exists(save_dir):
    os.makedirs(save_dir)
    


## Make to video ##
all_logdirs = os.listdir(extraction_dir)
with open('/media/kuser/datastore/nebula/pipelines/configs/entanglement_cfg.tml', 'r') as tmlfile:
    cfg = toml.load(tmlfile)

tracking_classes = cfg['entanglement']['deployed_classes']
idx2img = {}
class_label_map = {}
for idx, cat in enumerate(tracking_classes):
    class_label_map[cat] = idx
    
idx2cat = {v_i: v for v, v_i in class_label_map.items()}


for log_dir in ['/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/']:
    if os.path.isdir(os.path.join(extraction_dir, log_dir)):
        img_dir = os.path.join(extraction_dir, log_dir)
        
        # Resize images
        for im in sorted(os.listdir(img_dir)):
            try:
                
                if 'cfg' not in im or 'annotations' not in im:
                    print(os.path.join(os.path.join(extraction_dir, log_dir, im)))
                    img = cv2.imread(os.path.join(os.path.join(extraction_dir, log_dir, im)))
                    resized = cv2.resize(img, (320,192), interpolation = cv2.INTER_AREA) # resize to 320 x 192
                    cv2.imwrite( f"{os.path.join(os.path.join(extraction_dir, 'resized'), os.path.splitext(os.path.split(im)[-1])[0])}.jpg", resized)
            except:
                pass
                                
        
        
        img_dir = os.path.join(extraction_dir, 'resized')
        # Run Detections
        yolo_dir = "/media/kuser/datastore/nebula/pipelines/nets/yolov3/"
        anns_dir = os.path.join(os.path.abspath(img_dir), 'annotations')
        processed_dir = os.path.join(save_dir, log_dir, 'processed_frames')
        if True: # not os.path.exists(processed_dir):
            os.makedirs(processed_dir, exist_ok = True)
            
            uris = os.listdir('/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam8/cam--')
            uris = [os.path.join('/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam8/cam--', p) for p in sorted(uris)]

            
            dets = format_ultralytics_detections(img_dir)
            img2idx = {}
            idx2img = {}
            metadata = {}
            for idx, file in enumerate(sorted(uris)):
                file = path_leaf(file)
                img2idx[file] = idx
            idx2img = {v_i: v for v, v_i in img2idx.items()}

            for idx, (uri, img_dets) in enumerate(dets):
                bramboxes = []
                for box in img_dets:
                    det = Detection()
                    det.x_top_left = int(box['box2d']['x1'])
                    det.y_top_left = int(box['box2d']['y1'])
                    det.width = int(box['box2d']['x2'])- int(box['box2d']['x1']) + 1
                    det.height = int(box['box2d']['y2'])- int(box['box2d']['y1']) + 1
                    det.confidence = box['confidence']
                    if class_label_map is not None:
                        det.class_label = box['category']
                    else:
                        det.class_label = str(int(idx2cat[box['category']]))

                    bramboxes.append(det)

                
                    img_name = path_leaf(uris[img2idx[path_leaf(uri)]])
                    img = cv2.imread(uris[img2idx[path_leaf(uri)]])
                    image = vis.draw_boxes(img, bramboxes, show_labels=True)
                    cv2.imwrite( f"{os.path.join(processed_dir, os.path.splitext(os.path.split(img_name)[-1])[0])}.jpg", image)
                    

            # make video #
            log_video = "{}-cam{}.mp4".format(log_dir, cam_num)

            # Get Images
            exts = ['*.jpg', '*.png', '*.jpeg', '*.JPG']
            processed_imgs = [f for ext in exts for f in glob.glob(os.path.join(processed_dir, ext))] 
            if processed_imgs:
                clip = ImageSequenceClip(sorted(processed_imgs), fps = 30)
                clip.write_videofile(os.path.join(save_dir, log_video), audio=False)

                # Format Output Path
                HTML("""
                <video width="960" height="540" controls>
                 <source src="{0}">
                </video>
                """.format(save_dir))




# Get Frame Sequence
frame_sequence = []


/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000001.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000002.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000003.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000004.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000005.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000006.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000007.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000008.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000009.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000010.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000011.jpg
/media/kuser/datastor

/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000131.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000132.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000133.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000134.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000135.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000136.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000137.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000138.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000139.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000140.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000141.jpg
/media/kuser/datastor

/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000243.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000244.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000245.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000246.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000247.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000248.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000249.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000250.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000251.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000252.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000253.jpg
/media/kuser/datastor

/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000379.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000380.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000381.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000382.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000383.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000384.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000385.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000386.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000387.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000388.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000389.jpg
/media/kuser/datastor

/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000485.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000486.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000487.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000488.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000489.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000490.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000491.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000492.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000493.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000494.jpg
/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/00000495.jpg
/media/kuser/datastor

...

image 39427/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039427.jpg: Done. (0.020s)
image 39428/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039428.jpg: Done. (0.027s)
image 39429/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039429.jpg: Done. (0.024s)
image 39430/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039430.jpg: Done. (0.018s)
image 39431/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039431.jpg: Done. (0.017s)
image 39432/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039432.jpg: Done. (0.018s)
image 39433/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039433.jpg: Done. (0.018s)
image 39434/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039434.jpg: Done. (0.015s)
image 39435/39540 /media/kuser/datastore/nebula/pipelines/kache/

image 39499/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039499.jpg: Done. (0.034s)
image 39500/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039500.jpg: Done. (0.015s)
image 39501/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039501.jpg: Done. (0.023s)
image 39502/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039502.jpg: Done. (0.022s)
image 39503/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039503.jpg: Done. (0.017s)
image 39504/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039504.jpg: Done. (0.018s)
image 39505/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039505.jpg: Done. (0.017s)
image 39506/39540 /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/resized/00039506.jpg: Done. (0.015s)
image 39507/39540 /media/kuser/datastore/nebula/pipelines/kache/

t:   1%|▏         | 13/875 [00:00<00:06, 127.09it/s, now=None]

Moviepy - Building video /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/-cam7.mp4.
Moviepy - Writing video /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/-cam7.mp4



Moviepy - Done !
Moviepy - video ready /media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/-cam7.mp4


In [26]:
# Get Images
log_video = 'demo-lanenet-yolo.mp4'
exts = ['*.jpg', '*.png', '*.jpeg', '*.JPG']
imgs = os.listdir('/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/processed_frames/')

exts = ['*.jpg', '*.png', '*.jpeg', '*.JPG']
processed_imgs = [f for ext in exts for f in glob.glob(os.path.join('/media/kuser/datastore/nebula/pipelines/kache/frames/atm/cam7/Mine_project2/processed_frames/', ext))] 
if processed_imgs:
    clip = ImageSequenceClip(sorted(processed_imgs), fps = 30)
    clip.write_videofile(os.path.join(save_dir, log_video), audio=False)

    # Format Output Path
    HTML("""
    <video width="960" height="540" controls>
     <source src="{0}">
    </video>
    """.format(save_dir))

t:   0%|          | 0/39538 [00:00<?, ?it/s, now=None]

Moviepy - Building video /home/kuser/Desktop/demo_files/mp4cam7/demo-lanenet-yolo.mp4.
Moviepy - Writing video /home/kuser/Desktop/demo_files/mp4cam7/demo-lanenet-yolo.mp4




t:   5%|▌         | 2020/39538 [00:12<04:02, 154.86it/s, now=None]


t:  11%|█         | 4265/39538 [00:25<03:16, 179.70it/s, now=None]


t:  16%|█▌        | 6401/39538 [00:38<03:04, 179.90it/s, now=None]


...

t:  91%|█████████ | 36006/39538 [04:00<00:27, 126.78it/s, now=None]


t:  95%|█████████▌| 37612/39538 [04:12<00:17, 110.43it/s, now=None]


t:  98%|█████████▊| 38920/39538 [04:25<00:08, 74.49it/s, now=None]


t:   0%|          | 2/13903 [11:26<1325:17:19, 343.22s/it, now=None]A

Moviepy - Done !
Moviepy - video ready /home/kuser/Desktop/demo_files/mp4cam7/demo-lanenet-yolo.mp4
